# 기본세팅

In [1]:
### 한글 폰트 설치
!apt-get install -y fonts-nanum
!fc-cache -fv
!rm ~/.cache/matplotlib -rf
# 설치 후 colab의 경우 Runtime > Restart session 필요

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
fonts-nanum is already the newest version (20200506-1).
0 upgraded, 0 newly installed, 0 to remove and 0 not upgraded.
Font directories:
	/root/.local/share/fonts
	/usr/local/share/fonts
	/usr/share/fonts
	/root/.fonts
	/usr/share/fonts/truetype
	/usr/share/fonts/truetype/dejavu
	/usr/share/fonts/truetype/liberation
	/usr/share/fonts/truetype/nanum
/root/.local/share/fonts: skipping, no such directory
/usr/local/share/fonts: caching, new cache contents: 0 fonts, 0 dirs
/usr/share/fonts: caching, new cache contents: 0 fonts, 1 dirs
/usr/share/fonts/truetype: caching, new cache contents: 0 fonts, 3 dirs
/usr/share/fonts/truetype/dejavu: caching, new cache contents: 22 fonts, 0 dirs
/usr/share/fonts/truetype/liberation: caching, new cache contents: 16 fonts, 0 dirs
/usr/share/fonts/truetype/nanum: caching, new cache contents: 12 fonts, 0 dirs
/root/.fonts: skipping, no such directory
/usr/shar

In [2]:
import pandas as pd
import matplotlib as mpl
import matplotlib.dates as mdates
import matplotlib.pyplot as plt
mpl.rc('font', family='NanumBarunGothic') # 혹은 다른 설치한 Nanum 폰트 사용
import matplotlib.font_manager as fm
# 설치된 폰트 중 'NanumGothic' 찾기
for font in fm.fontManager.ttflist:
    if 'NanumGothic' in font.name:
        plt.rcParams['font.family'] = font.name
        break
plt.rcParams['axes.unicode_minus'] = False
import seaborn as sns
import numpy as np
import scipy.stats as stats

# 서비스 방향 모색을 위한 분석
## 분석 목적 : 설정된 페르소나에 맞춤형 프로그램 제공을 위한 서비스 방향 모색
- 페르소나 : 희귀 신경계 질환을 앓고 있으며, 취사/청소 능력이 없는 서울 소재의 70대 독거 남성 

### 분석 방향
1) 신경계통 질환 환자들의 니즈 파악

#### 전체 희귀질환 환자들의 니즈 파악

##### dataset 불러오기
< 전체 dataset >
- KMSS(한국다발성경화증협회)
- dcinside(디시인사이드)
- behcet(한국베체트환우협회)
- kfrd(한국희귀질환재단)
- kord((사)한국희귀. 난치성질환연합회)
- VonRecklinghausen(신경섬유종증환우)
- gowithms(MASTERING MS 다발성경화증 '행복한 동행')
- guillainbarre(길랑바레, 밀러피셔 증후군)
- neurofibromatosis(2형 신경섬유종)
- parkinsons(파킨슨병)
- parkinsons_two(파킨슨병)
- rheumatism(강인함(강직성척추염연합회))
- navercafe ...

In [3]:
# mongo에서 db 불러오는 함수
import pymongo
def dbconnect(collection) :
    client=pymongo.MongoClient('mongodb://trainings.iptime.org',45003)
    db= client['data_analysis']
    collection = db[collection]
    data = collection.find()
    df = pd.DataFrame(data)
    return df

In [4]:
# 중복값 제거하는 함수(contents를 기준으로)
def drop_duplicates(df, contents) : 
    df.drop_duplicates(subset=contents, keep='first', inplace=True)
    df.reset_index(drop=True, inplace=True)
    return df

In [5]:
# 특정 열에서 list를 str으로 변환하는 함수
def list_join(row) :
    row = ' '.join(row)
    return row

In [6]:
# 특정 열에서 \n 삭제하는 함수
def remove_text(row) :
    row = row.replace(r'\n',' ')
    return row

##### 데이터 전처리

###### naver_cafe_dongchul

In [7]:
df_dongchul = dbconnect("naver_cafe_dongchul")
df_dongchul

_id    dise_name dise_code  \
0     66417aadc68fb6f104417c71       중증근무력증     G70.0   
1     66417ab5c68fb6f104417c73       중증근무력증     G70.0   
2     66417abcc68fb6f104417c75       중증근무력증     G70.0   
3     66417ac4c68fb6f104417c77       중증근무력증     G70.0   
4     66417acbc68fb6f104417c79       중증근무력증     G70.0   
...                        ...          ...       ...   
3794  664311c21bfc116b6fb2e233  모세혈관확장성운동실조     G11.3   
3795  664311c91bfc116b6fb2e234  모세혈관확장성운동실조     G11.3   
3796  664311d11bfc116b6fb2e235  모세혈관확장성운동실조     G11.3   
3797  664311d81bfc116b6fb2e236  모세혈관확장성운동실조     G11.3   
3798  664311df1bfc116b6fb2e237  모세혈관확장성운동실조     G11.3   

                                      cafe  \
0                             ♥시험관아기 대표카페♥   
1     건강한 리서치 건강/ 미용/ 맛집 /서울 강남구 송파구 강서구 등   
2          스마트홀릭 ㅣ스사사맘스홀릭중고나라 여우야 딜공디매쇼핑테무   
3                               고양이라서 다행이야   
4                          폐암환우들과 그 가족의 모임   
...                                    ...   
3794                                   옻사랑   
3795                              한국규사모연합회   
3796                         국제의료관광 / 해동우남   
3797       임성균의 [Occupational Therapy Lab]   
3798                     치료 잘하는 미올한의원(대구점)   

                                        title       name               date  \
0     혹시, 복시(겹쳐보임)가 있거나 중증근무력증 진단 받으신 분 계실까요?     설탕친토마토  2024.03.20. 08:43   
1      중증근무력증 치료 전문병원 시설 좋은곳 어디인지 아세요?(자료수집중)       자료정리  2024.05.01. 22:02   
2                     근력이 저하되는 중증 근무력증 알아 봅니다      미소의마법  2024.04.28. 08:28   
3                                     중증 근무력증        쌔랄라  2023.07.21. 18:19   
4                     항암중 중증근무력증 치료하신 분 계신가요?        묘성연  2023.08.30. 21:40   
...                                       ...        ...                ...   
3794                        암을 예방하려면 체온을 높여라!       생명나무  2012.04.25. 20:18   
3795                             작용기전 11 ~ 15  규소를사랑하는모임  2017.09.29. 00:15   
3796           부어서 퉁퉁해진 얼굴, 탱탱해진 다리에 좋은 특효 음식        현인선  2013.12.05. 14:52   
3797                                 필수 의학용어1        작돌이  2014.10.05. 03:41   
3798                 삼성동 한방 물리치료 신반포역 교통사고 치료   82232400  2021.04.07. 05:10   

                                               contents  \
0     안녕하세요.\n채취 2회, 동결 5차를 앞두고 있습니다.\n얼마전? 그 이전부터 초...   
1     반갑습니다 ^^ 카페 여러분들 항상 잘 계시죠?\n이번 리서치는 중증근무력증 치료 ...   
2     근력이 저하되는 중증 근무력증은 근력이 감소하여 근육이 약해지고 기능이 저하되는 질...   
3     저희 아이가 최근 갑작스럽게 아파 입원중 입니다\nmri,ct 모두 정상이라 나오고...   
4     아버지께서 비소세포 편평상피 치료 4년차이십니다.\n20년도에 키트루다로 시작해서 ...   
...                                                 ...   
3794  Part4.암 예방 운동법\n암, 잡을 수 있다! 최고 명의들의 암예방 생활법\n주...   
3795                                제3장 규소의 작용 기전\n\...   
3796     자동차에는 연료, 윤활유, 냉각수 같은 액체가 있어 엔진을 돌아가게 한다. 우...   
3797  digestive system : 소화기계\noral cavity : 구강\ning...   
3798  존재하지 않는 이미지입니다.\n#삼성동 한방 물리치료 야간동통과 같은 특징적인 통증...   

                                                 review  
0     [신경과에서 소론도정 처방받아서 증상 조절하고 있어요. 저같은 경우는 자연적으로 없...  
1     [중증근무력증 관련정보 찾는분 은근 계신것 같더라고요 다른 회원님들께 여쭤보시면 될...  
2     [▶테무 50만원 무료쇼핑 할인코드 ▶https://temu.com/s/1d3vDj...  
3     [바이러스 관련 가능성이 있으니\n\n그 쪽으로 사람 질병으로 검색도 해보세요..\...  
4     [복시가 있나요????전신중증근무력증은 초기에 복시가\n먼저 시작되는 경우가 많습니...  
...                                                 ...  
3794                                                     
3795                                                     
3796                                                     
3797                                                     
3798                                                     

[3799 rows x 9 columns]

In [8]:
# 중복데이터 확인
df_dongchul['contents'].value_counts()
# 중복데이터 없음

contents
오늘은 포근한 하루 였네요 계곡에서는\n봄이 다가 온다는 느낌이 들려요 얼음이 녹으면서\n시냇물도 졸졸 흐르는 소리가 들리네요\n행복하고 즐거운 휴일 저녁시간 보내세요\n'근육 약화' 현상은 근육이 허약해서 일어나는 피로 또는\n탈진 현상으로 근육 또는 신경 근육 질환 증상이다.\n근육이 약해지면 의자에서 일어나거나,\n계단을 오르거나, 병 뚜껑을 따는 것이 예전보다 힘들 수도 있다.\n때문에 이같은 질환을 겪는 환자들은 무기력해지기 쉽다.\n근육 약화는 갑자기 생기기도 하지만,\n대부분의 경우 시간이 지남에 따라 조금씩 영향을 미치는 경우가 더 많다.\n그래서 의식하지 못하는 사이 갑자기 생긴 증상처럼 느껴지는 경우도 있다.\n미국 건강매체 웹엠디는 "근육의 약화는 피로나 통증과는 다르다."고 지적한다.\n피로나 통증은 휴식이나 치료로 단기간에 치료될 수도 있지만 근육 약화는 장기적인 노력을 필요로 할 수 있다.\n근육감소증 속도 지나치면 건강 문제 일으킬 수도\n웹엠디는 최근 근육 약화를 일으키는 몇 가지 원인들을 소개했다.\n가장 대표적인 것은 '노화'다.\n나이가 들면서 근육량이 좀 줄고 약해지는 것은 정상이다.\n의사들은 이것을 근육감소증이라고 부른다. 60대나 70대 이전에는 잘 알아차리지 못할 수 있다.\n다만 속도가 지나치게 빠르다면 병원에 가서 진단을 받아봐야 한다.\n만약 당신이 근육에서 힘이 빠지고 있다고 느끼고 있으며,\n심각한 건강 문제의 징후일 수 있기 때문이다.\n근육 약화를 수반하는 증상으로는\n수면장애, 갑상선 질환, 만성피로증후군, 피부근염, 다발성근육염, 기타 근질환 등이 있다.\n중증 근무력증, 심부전, 당뇨병과 같은 질병들도 근육 약화를 동반하는 경우가 있다.\n이밖에도 근육 약화는 다발성 경화증(Multiple Sclerosis: MS)과 같은 심각한 질환을 나타내는 신호일 수 있다.\n다발성 경화증에 걸리면, 면역체계가 신경섬유를 둘러싸고 있는 보호막을 공격하고,\n뇌와 신체의 다른 부분들 사이의 의사소

In [9]:
df_dongchul.reset_index(drop=True, inplace=True)
df_dongchul

_id    dise_name dise_code  \
0     66417aadc68fb6f104417c71       중증근무력증     G70.0   
1     66417ab5c68fb6f104417c73       중증근무력증     G70.0   
2     66417abcc68fb6f104417c75       중증근무력증     G70.0   
3     66417ac4c68fb6f104417c77       중증근무력증     G70.0   
4     66417acbc68fb6f104417c79       중증근무력증     G70.0   
...                        ...          ...       ...   
3794  664311c21bfc116b6fb2e233  모세혈관확장성운동실조     G11.3   
3795  664311c91bfc116b6fb2e234  모세혈관확장성운동실조     G11.3   
3796  664311d11bfc116b6fb2e235  모세혈관확장성운동실조     G11.3   
3797  664311d81bfc116b6fb2e236  모세혈관확장성운동실조     G11.3   
3798  664311df1bfc116b6fb2e237  모세혈관확장성운동실조     G11.3   

                                      cafe  \
0                             ♥시험관아기 대표카페♥   
1     건강한 리서치 건강/ 미용/ 맛집 /서울 강남구 송파구 강서구 등   
2          스마트홀릭 ㅣ스사사맘스홀릭중고나라 여우야 딜공디매쇼핑테무   
3                               고양이라서 다행이야   
4                          폐암환우들과 그 가족의 모임   
...                                    ...   
3794                                   옻사랑   
3795                              한국규사모연합회   
3796                         국제의료관광 / 해동우남   
3797       임성균의 [Occupational Therapy Lab]   
3798                     치료 잘하는 미올한의원(대구점)   

                                        title       name               date  \
0     혹시, 복시(겹쳐보임)가 있거나 중증근무력증 진단 받으신 분 계실까요?     설탕친토마토  2024.03.20. 08:43   
1      중증근무력증 치료 전문병원 시설 좋은곳 어디인지 아세요?(자료수집중)       자료정리  2024.05.01. 22:02   
2                     근력이 저하되는 중증 근무력증 알아 봅니다      미소의마법  2024.04.28. 08:28   
3                                     중증 근무력증        쌔랄라  2023.07.21. 18:19   
4                     항암중 중증근무력증 치료하신 분 계신가요?        묘성연  2023.08.30. 21:40   
...                                       ...        ...                ...   
3794                        암을 예방하려면 체온을 높여라!       생명나무  2012.04.25. 20:18   
3795                             작용기전 11 ~ 15  규소를사랑하는모임  2017.09.29. 00:15   
3796           부어서 퉁퉁해진 얼굴, 탱탱해진 다리에 좋은 특효 음식        현인선  2013.12.05. 14:52   
3797                                 필수 의학용어1        작돌이  2014.10.05. 03:41   
3798                 삼성동 한방 물리치료 신반포역 교통사고 치료   82232400  2021.04.07. 05:10   

                                               contents  \
0     안녕하세요.\n채취 2회, 동결 5차를 앞두고 있습니다.\n얼마전? 그 이전부터 초...   
1     반갑습니다 ^^ 카페 여러분들 항상 잘 계시죠?\n이번 리서치는 중증근무력증 치료 ...   
2     근력이 저하되는 중증 근무력증은 근력이 감소하여 근육이 약해지고 기능이 저하되는 질...   
3     저희 아이가 최근 갑작스럽게 아파 입원중 입니다\nmri,ct 모두 정상이라 나오고...   
4     아버지께서 비소세포 편평상피 치료 4년차이십니다.\n20년도에 키트루다로 시작해서 ...   
...                                                 ...   
3794  Part4.암 예방 운동법\n암, 잡을 수 있다! 최고 명의들의 암예방 생활법\n주...   
3795                                제3장 규소의 작용 기전\n\...   
3796     자동차에는 연료, 윤활유, 냉각수 같은 액체가 있어 엔진을 돌아가게 한다. 우...   
3797  digestive system : 소화기계\noral cavity : 구강\ning...   
3798  존재하지 않는 이미지입니다.\n#삼성동 한방 물리치료 야간동통과 같은 특징적인 통증...   

                                                 review  
0     [신경과에서 소론도정 처방받아서 증상 조절하고 있어요. 저같은 경우는 자연적으로 없...  
1     [중증근무력증 관련정보 찾는분 은근 계신것 같더라고요 다른 회원님들께 여쭤보시면 될...  
2     [▶테무 50만원 무료쇼핑 할인코드 ▶https://temu.com/s/1d3vDj...  
3     [바이러스 관련 가능성이 있으니\n\n그 쪽으로 사람 질병으로 검색도 해보세요..\...  
4     [복시가 있나요????전신중증근무력증은 초기에 복시가\n먼저 시작되는 경우가 많습니...  
...                                                 ...  
3794                                                     
3795                                                     
3796                                                     
3797                                                     
3798                                                     

[3799 rows x 9 columns]

In [10]:
# 각 컬럼별 전처리(제목)
df_dongchul['title']

0       혹시, 복시(겹쳐보임)가 있거나 중증근무력증 진단 받으신 분 계실까요?
1        중증근무력증 치료 전문병원 시설 좋은곳 어디인지 아세요?(자료수집중)
2                       근력이 저하되는 중증 근무력증 알아 봅니다
3                                       중증 근무력증
4                       항암중 중증근무력증 치료하신 분 계신가요?
                         ...                   
3794                          암을 예방하려면 체온을 높여라!
3795                               작용기전 11 ~ 15
3796             부어서 퉁퉁해진 얼굴, 탱탱해진 다리에 좋은 특효 음식
3797                                   필수 의학용어1
3798                   삼성동 한방 물리치료 신반포역 교통사고 치료
Name: title, Length: 3799, dtype: object

In [11]:
# 각 컬럼별 전처리(내용)
# 특정 열에서 \n 삭제
df_dongchul['contents'] = df_dongchul['contents'].str.replace('\n', '')

df_dongchul['contents']

0       안녕하세요.채취 2회, 동결 5차를 앞두고 있습니다.얼마전? 그 이전부터 초점이 안...
1       반갑습니다 ^^ 카페 여러분들 항상 잘 계시죠?이번 리서치는 중증근무력증 치료 추천...
2       근력이 저하되는 중증 근무력증은 근력이 감소하여 근육이 약해지고 기능이 저하되는 질...
3       저희 아이가 최근 갑작스럽게 아파 입원중 입니다mri,ct 모두 정상이라 나오고중증...
4       아버지께서 비소세포 편평상피 치료 4년차이십니다.20년도에 키트루다로 시작해서 2년...
                              ...                        
3794    Part4.암 예방 운동법암, 잡을 수 있다! 최고 명의들의 암예방 생활법주 5회 ...
3795                                  제3장 규소의 작용 기전11....
3796       자동차에는 연료, 윤활유, 냉각수 같은 액체가 있어 엔진을 돌아가게 한다. 우...
3797    digestive system : 소화기계oral cavity : 구강ingesti...
3798    존재하지 않는 이미지입니다.#삼성동 한방 물리치료 야간동통과 같은 특징적인 통증 양...
Name: contents, Length: 3799, dtype: object

In [12]:
# 각 컬럼별 전처리(댓글)
# 특정 열에서 \n 삭제
df_dongchul['reply'] = df_dongchul['reply'].str.replace('\n', '')
# 날짜와 고유명사 삭제
df_dongchul['reply'] = df_dongchul['reply'].str.replace(r'\b\w+\d{4}\.\d{2}\.\d{2}\s+\d{2}:\d{2}:\d{2}', '', regex=True)

df_dongchul['reply']

KeyError: 'reply'

In [ ]:
dongchul_series = df_dongchul['title'] + ' ' + df_dongchul['contents']
dongchul_series.isna().sum()

In [ ]:
# title, contents, reply 컬럼을 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
dongchul_series = df_dongchul['title'] + ' ' + df_dongchul['contents']
dongchul_list = dongchul_series.tolist()
dongchul_list

###### naver_cafe_yugyeong

In [ ]:
df_yugyeong = dbconnect("naver_cafe_yugyeong")
df_yugyeong

In [99]:
# 중복데이터 확인
df_dcinside_raredisease['contents'].value_counts()
df_dcinside_raredisease.drop_duplicates(subset="contents", keep='first', inplace=True)
df_dcinside_raredisease['contents'].value_counts()
df_dcinside_raredisease.reset_index(drop=True, inplace=True)
df_dcinside_raredisease['contents'].value_counts()
# 중복데이터 없음

contents
꾹                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               1
피부랑 똑같은색으로 점있는 부분만 문신하면 티는 조금 나겠지만 조금은 희미해질듯                                                                                                                                                                                                                                                                                                                                                                                                 

In [100]:
#각 컬럼별 전처리(제목)
df_dcinside_raredisease['title']

0        갑자기든 생각인데 신섬 반점 문신으로 가릴수있지않을까?
1      영국, 부작용 이슈 퀴놀론계 항생제 모든질환 1차사용 금지
2                검사 받는 병원 근처 지역 병원으로 바꿈
3                   섬유종 수술은 아산병원이 젤 나음?
4           신섬 증상 별로 안 심하면 코셀루고 약 못 먹나?
                     ...               
480                            희귀병 걸렸다ㅜ
481                희귀병이니 갤마저 글이 희귀하네...
482                                 힘들다
483                           좋은 일 하십니다
484                                 발도잔
Name: title, Length: 485, dtype: object

In [105]:
#각 컬럼별 전처리(내용)
# 특정 열에서 \n 삭제
df_dcinside_raredisease['contents'] = df_dcinside_raredisease['contents'].str.replace(r'\n', '')
df_dcinside_raredisease['contents'] = df_dcinside_raredisease['contents'].str.replace(r'\\n', '')
df_dcinside_raredisease['contents']

0           피부랑 똑같은색으로 점있는 부분만 문신하면 티는 조금 나겠지만 조금은 희미해질듯
1      https://www.newsthevoice.com/news/articleView....
2      계속 서울로 정기검진 받으러 가다가 어제를 마지막으로 그냥 집근처에 있는 지방 대학...
3                                               좀 큰 부위인데
4      엄청 심한건 아닌 거 같은데...먹어보고싶다..작년 여름엔 머리랑 눈이 너무 아파서...
                             ...                        
480               베체트 ㅆㅂ 이거 뭐야?확진줘놓고 아프면 오라니 이게 말이냐?방구냐?
481                자주 들를게 나도 희귀병 환우얍 흑 - dc official App
482    병명찾기 몇년째인지정말 사람들 말대로 다 내 머릿속에 있는건지아님 정말 원인이 있는...
483              실제로 환우들이 여기를 사용할지는 모르겠다만 모두들 힘내십쇼. 화이팅!
484                                                    꾹
Name: contents, Length: 485, dtype: object

In [108]:
# title, contents, reply 컬럼을 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
dcinside_series = df_dcinside_raredisease['title'] + ' ' + df_dcinside_raredisease['contents']
dcinside_series.isna().sum()
dcinside_series.dropna()

0      갑자기든 생각인데 신섬 반점 문신으로 가릴수있지않을까? 피부랑 똑같은색으로 점있는 ...
1      영국, 부작용 이슈 퀴놀론계 항생제 모든질환 1차사용 금지 https://www.n...
2      검사 받는 병원 근처 지역 병원으로 바꿈 계속 서울로 정기검진 받으러 가다가 어제를...
3                           섬유종 수술은 아산병원이 젤 나음? 좀 큰 부위인데
4      신섬 증상 별로 안 심하면 코셀루고 약 못 먹나? 엄청 심한건 아닌 거 같은데......
                             ...                        
480      희귀병 걸렸다ㅜ 베체트 ㅆㅂ 이거 뭐야?확진줘놓고 아프면 오라니 이게 말이냐?방구냐?
481    희귀병이니 갤마저 글이 희귀하네... 자주 들를게 나도 희귀병 환우얍 흑 - dc ...
482    힘들다 병명찾기 몇년째인지정말 사람들 말대로 다 내 머릿속에 있는건지아님 정말 원인...
483    좋은 일 하십니다 실제로 환우들이 여기를 사용할지는 모르겠다만 모두들 힘내십쇼. 화이팅!
484                                                발도잔 꾹
Length: 483, dtype: object

In [109]:
dcinside_list = dcinside_series.tolist()
dcinside_list

['갑자기든 생각인데 신섬 반점 문신으로 가릴수있지않을까? 피부랑 똑같은색으로 점있는 부분만 문신하면 티는 조금 나겠지만 조금은 희미해질듯',
 '영국, 부작용 이슈 퀴놀론계 항생제 모든질환 1차사용 금지 https://www.newsthevoice.com/news/articleView.html?idxno=36427 영국, 부작용 이슈 퀴놀론계 항생제 모든질환 1차사용 금지영국 의약품규제청은 플루오로퀴놀론계열 항생제가 다른 계열의 항생제에 부적절한 경우에만 처방토록 아예 1차요법 사용을 금지시켰다.영국 의약품규제청(MHRA)는 지난 22일 경구, 주사 또는 흡입을 통해 전신에 투여되는 플루오로키놀론계열 항생제는 사용하기에 적합한 다른 항생제가 없는 경우로 제한키로 했다고 발표했다.이는 2019년 일부 심각하지 않은 감염이나 전립선염 등 비세균성 질환에 대한 1차 사용금지에도 불구 이상반응 보고가 지속되고 처방패턴의 변화가 없음에 따라 시행되는 추가조치다.MHRA는 이번 조치는 부작용을 줄이기 위해 진www.newsthevoice.comhttps://www.yakup.com/news/index.html?mode=view&cat=16&nid=281566EU, 플루오로퀴놀론系 항생제 제한적 사용 요망나 아는 놈은 알텐데 약 잘못 먹고 인생 조진 놈임',
 '검사 받는 병원 근처 지역 병원으로 바꿈 계속 서울로 정기검진 받으러 가다가 어제를 마지막으로 그냥 집근처에 있는 지방 대학병원 가는거오 했음..뭐 지방 병원도 큰 차이는 없겠지?',
 '섬유종 수술은 아산병원이 젤 나음? 좀 큰 부위인데',
 '신섬 증상 별로 안 심하면 코셀루고 약 못 먹나? 엄청 심한건 아닌 거 같은데...먹어보고싶다..작년 여름엔 머리랑 눈이 너무 아파서 신경과 가서 CT찍었더니뇌에 종양 있다 그랬고쇄골이나ㅜ등에도 종양 새로 생기고 있던데증상 엄청 심한 환우분들만 먹는거야??일단 소아 환우들 먼저 처방 가능한거 같은데..- dc official App',
 '루게릭병 전조증상이 느껴져요 발

###### behcet

In [115]:
df_behcet = dbconnect("persona1_behcet_freeboard")
df_behcet

_id   contents_title contents_writer  \
0      6631f76c5bc2b816b6c98c6c         어느봄날에...             배영반   
1      6631f7835bc2b816b6c98c6d  세상에서 가장 좋은 이별이란             한현옥   
2      6631f7855bc2b816b6c98c6e             사람살려             한현옥   
3      6631f7875bc2b816b6c98c6f           봄이 왔어요             한현옥   
4      6631f7875bc2b816b6c98c70   신년맞이 떡국떡 감사의 글             이재강   
...                         ...              ...             ...   
38573  6632c1545bc2b816b6ca2319   사랑전선에 또 문제가...             이은희   
38574  6632c1565bc2b816b6ca231a   사랑전선에 또 문제가...             이은희   
38575  6632c1575bc2b816b6ca231b   사랑전선에 또 문제가...             이은희   
38576  6632c1585bc2b816b6ca231c   사랑전선에 또 문제가...             이은희   
38577  6632c1595bc2b816b6ca231d   사랑전선에 또 문제가...             이은희   

      contents_date  click_count  \
0        2024.04.07           19   
1        2024.03.19           19   
2        2024.03.01           22   
3        2024.02.27           16   
4        2024.02.01           13   
...             ...          ...   
38573    2005.04.12           82   
38574    2005.04.12           82   
38575    2005.04.12           82   
38576    2005.04.12           82   
38577    2005.04.12           82   

                                           contents_text  \
0      한참  몸이 않좋아 열심히 치료하다\n잠시 한숨을 돌립니다.\n\n요즘 집압 공원에...   
1      폐암말기로 투병하던 길똥씨..\n방사선을 머리에 쐬여 영혼마저 암세포와 함께 파쇄됐...   
2         00:00\n     00:00\n           \n옻순을 얼마나 좋아하...   
3      봄에 심을 햇강낭콩을 종류대로 사려고 오일장만 서면 가서 눈여겨 보았었다.\n작년....   
4      할리데이비슨 할리천사와 코리아챕터 감사드립니다~\n\n선정해주신 환우회 임원님들과 ...   
...                                                  ...   
38573  참 공감가네요!저두 두달전에...헤어졌답니다!첨 만날때부터 걱정은 됐지만...괜찮을...   
38574  참 공감가네요!저두 두달전에...헤어졌답니다!첨 만날때부터 걱정은 됐지만...괜찮을...   
38575  참 공감가네요!저두 두달전에...헤어졌답니다!첨 만날때부터 걱정은 됐지만...괜찮을...   
38576  참 공감가네요!저두 두달전에...헤어졌답니다!첨 만날때부터 걱정은 됐지만...괜찮을...   
38577  참 공감가네요!저두 두달전에...헤어졌답니다!첨 만날때부터 걱정은 됐지만...괜찮을...   

                                              reply_list  
0      [이재강 2024.04.10\n답변\n오~~뚱뚱해 보여요,, 각도 비스듬이 해서 찍...  
1                         [이재강 2024.03.19\n답변\n잘 읽었습니다.]  
2                                                     []  
3          [이재강 2024.02.27\n답변\n^^ 몸 생각하셔서 쉬엄쉬엄 농사 지으세요]  
4                                                     []  
...                                                  ...  
38573                   [2005.04.13\n답변 삭제\n화이티잉~~~ 얍!!]  
38574                   [2005.04.13\n답변 삭제\n화이티잉~~~ 얍!!]  
38575                   [2005.04.13\n답변 삭제\n화이티잉~~~ 얍!!]  
38576                   [2005.04.13\n답변 삭제\n화이티잉~~~ 얍!!]  
38577                   [2005.04.13\n답변 삭제\n화이티잉~~~ 얍!!]  

[38578 rows x 7 columns]

In [ ]:
# 중복값 제거 후 확인
df_behcet = drop_duplicates(df_behcet, 'contents_text')
df_behcet['contents_text'].value_counts()

In [ ]:
# 각 컬럼별 전처리(제목)
df_behcet['contents_title']

In [ ]:
# 각 컬럼별 전처리(내용)
df_behcet.loc[:,'contents_text'] = df_behcet['contents_text'].apply(remove_text)
df_behcet

In [ ]:
behcet_list = behcet_series.tolist()
behcet_list

###### kfrd

In [ ]:
df_kfrd = dbconnect("persona1_kfrd_freeboard")
df_kfrd

In [ ]:
# 중복값 제거
df_kfrd = drop_duplicates(df_kfrd, 'contents_text')

In [ ]:
# 각 컬럼별 전처리(제목)
df_kfrd['contents_title']

In [ ]:
# 're;' 또는 'RE:'를 포함한 텍스트 삭제
df_kfrd['contents_title'] = df_kfrd['contents_title'].str.replace(r're;\s*', '', regex=True)
df_kfrd['contents_title'] = df_kfrd['contents_title'].str.replace(r'RE:\s*', '', regex=True)
df_kfrd['contents_title'] = df_kfrd['contents_title'].str.replace(r're:\s*', '', regex=True)
df_kfrd['contents_title']

In [ ]:
# 각 컬럼별 전처리(제목)
df_kfrd['contents_text']

In [ ]:
df_kfrd.loc[:,'contents_text'] = df_kfrd['contents_text'].apply(remove_text)
df_kfrd

In [ ]:
# contents_title, contents_text 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
kfrd_series = df_kfrd['contents_title'] + ' ' + df_kfrd['contents_text']
kfrd_series.isna().sum()

In [ ]:
kfrd_list = kfrd_series.tolist()
kfrd_list

###### kord

In [ ]:
df_kord = dbconnect("persona1_kord_freeboard")
df_kord

In [ ]:
# 중복값 제거
df_kord = drop_duplicates(df_kord, 'contents_text')

In [ ]:
# 각 컬럼별 전처리(제목)
df_kord['contents_title']

In [ ]:
# 're;' 또는 'RE:'를 포함한 텍스트 삭제
df_kord['contents_title'] = df_kord['contents_title'].str.replace(r're;\s*', '', regex=True)
df_kord['contents_title'] = df_kord['contents_title'].str.replace(r'RE:\s*', '', regex=True)
df_kord['contents_title'] = df_kord['contents_title'].str.replace(r're:\s*', '', regex=True)
df_kord['contents_title'] = df_kord['contents_title'].str.replace(r'Re:\s*', '', regex=True)
df_kord['contents_title']

In [ ]:
# 각 컬럼별 전처리(내용)
df_kord['contents_text']

In [ ]:
df_kord.loc[:,'contents_text'] = df_kord['contents_text'].apply(remove_text)
df_kord

In [ ]:
# contents_title, contents_text 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
kord_series = df_kord['contents_title'] + ' ' + df_kord['contents_text']
kord_series.isna().sum()

In [ ]:
kord_list = kord_series.tolist()
kord_list

###### VonRecklinghausen

In [ ]:
df_VonRecklinghausen = dbconnect("persona1_navercafe_VonRecklinghausen")
df_VonRecklinghausen

In [ ]:
# 중복값 제거
df_VonRecklinghausen = drop_duplicates(df_VonRecklinghausen, 'contents')

In [ ]:
# 각 컬럼별 전처리(제목)
df_VonRecklinghausen['title']

In [ ]:
# 각 컬럼별 전처리(내용)
df_VonRecklinghausen['contents']

In [ ]:
df_VonRecklinghausen.loc[:,'contents'] = df_VonRecklinghausen['contents'].apply(remove_text)
df_VonRecklinghausen

In [ ]:
# title, contents 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
VonRecklinghausen_series = df_VonRecklinghausen['title'] + ' ' + df_VonRecklinghausen['contents']
VonRecklinghausen_series.isna().sum()

In [ ]:
VonRecklinghausen_list = VonRecklinghausen_series.tolist()
VonRecklinghausen_list

###### gowithms

In [ ]:
df_gowithms = dbconnect("persona1_navercafe_gowithms")
df_gowithms

In [ ]:
# 중복값 제거
df_gowithms = drop_duplicates(df_gowithms, 'contents')

In [ ]:
# 각 컬럼별 전처리(제목)
df_gowithms['title']

In [ ]:
# '📰 희귀질환 최신 뉴스 모음 💚' 와 같은 정기적인 광고글 확인
# '희귀질환 최신 뉴스 모음'이라는 내용이 담겨있는 행(row) 삭제
df_gowithms = df_gowithms[~df_gowithms['title'].str.contains('희귀질환 최신 뉴스 모음')]

df_gowithms

In [ ]:
# 각 컬럼별 전처리(내용)
df_gowithms['contents']

In [ ]:
df_gowithms.loc[:,'contents'] = df_gowithms['contents'].apply(remove_text)
df_gowithms

In [ ]:
# 쓸데없는 광고글 drop
filtered_rows = df_gowithms[df_gowithms['contents'].str.contains('중고차수출')]
print(filtered_rows['contents'])

In [ ]:
# 쓸데없는 광고글 drop
df_gowithms = df_gowithms[~df_gowithms['contents'].str.contains('중고차수출')]
df_gowithms = df_gowithms[~df_gowithms['contents'].str.contains('레어노트')]
df_gowithms = df_gowithms[~df_gowithms['contents'].str.contains('PLEASE COME AND JOIN')]
df_gowithms = df_gowithms[~df_gowithms['contents'].str.contains('카지노')]
df_gowithms = df_gowithms[~df_gowithms['contents'].str.contains('shapetype')]
df_gowithms

In [ ]:
# contents_title, contents_text 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
gowithms_series = df_gowithms['title'] + ' ' + df_gowithms['contents']
gowithms_series.isna().sum()

In [ ]:
gowithms_list = gowithms_series.tolist()
gowithms_list

###### guillainbarre

In [ ]:
df_guillainbarre = dbconnect("persona1_navercafe_guillainbarre")
df_guillainbarre

In [ ]:
# 중복값 제거
df_guillainbarre = drop_duplicates(df_guillainbarre, 'contents')

In [ ]:
# 각 컬럼별 전처리(제목)
df_guillainbarre['title']

In [ ]:
# 각 컬럼별 전처리(내용)
df_guillainbarre['contents']

In [ ]:
# 광고글 drop
df_guillainbarre = df_guillainbarre[~df_guillainbarre['contents'].str.contains('레어노트')]

In [ ]:
df_guillainbarre.loc[:,'contents'] = df_guillainbarre['contents'].apply(remove_text)
df_guillainbarre

In [ ]:
# title, contents 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
guillainbarre_series = df_guillainbarre['title'] + ' ' + df_guillainbarre['contents']
guillainbarre_series.isna().sum()

In [ ]:
guillainbarre_list = guillainbarre_series.tolist()
guillainbarre_list

###### neurofibromatosis

In [ ]:
df_neurofibromatosis = dbconnect("persona1_navercafe_neurofibromatosis")
df_neurofibromatosis

In [ ]:
# 중복값 제거
df_neurofibromatosis = drop_duplicates(df_neurofibromatosis, 'contents')

In [ ]:
# 각 컬럼별 전처리(제목)
df_neurofibromatosis['title']

In [ ]:
# 각 컬럼별 전처리(내용)
df_neurofibromatosis['contents']

In [ ]:
df_neurofibromatosis.loc[:,'contents'] = df_neurofibromatosis['contents'].apply(remove_text)
df_neurofibromatosis

In [ ]:
# contents_title, contents_text 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
neurofibromatosis_series = df_neurofibromatosis['title'] + ' ' + df_neurofibromatosis['contents']
neurofibromatosis_series.isna().sum()

In [ ]:
neurofibromatosis_list = neurofibromatosis_series.tolist()
neurofibromatosis_list

###### rheumatism

In [ ]:
df_rheumatism = dbconnect("persona1_navercafe_rheumatism")
df_rheumatism

In [ ]:
# 중복값 제거
df_rheumatism = drop_duplicates(df_rheumatism, 'contents')

In [ ]:
# 각 컬럼별 전처리(제목)
df_rheumatism['title']

In [ ]:
# 각 컬럼별 전처리(내용)
df_rheumatism['contents']

In [ ]:
df_rheumatism.loc[:,'contents'] = df_rheumatism['contents'].apply(remove_text)
df_rheumatism

In [ ]:
# title, contents 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
rheumatism_series = df_rheumatism['title'] + ' ' + df_rheumatism['contents']
rheumatism_series.isna().sum()

In [ ]:
rheumatism_list = rheumatism_series.tolist()
rheumatism_list

###### navercafe - 희귀 신경계 질환

In [13]:
df_rare_nervous_disorder01 = dbconnect("naver_cafe_Sympton")
df_rare_nervous_disorder02 = dbconnect("naver_cafe_dongchul")
df_rare_nervous_disorder03 = dbconnect("naver_cafe_yugyeong")
df_rare_nervous_disorder04 = dbconnect("naver_cafe_yujin")
df_rare_nervous_disorder05 = dbconnect("naver_cafe_jisu")

In [14]:
# null값 확인
df_rare_nervous_disorder01.isna().sum()

Series([], dtype: float64)

In [15]:
df_rare_nervous_disorder02.isna().sum()

_id          0
dise_name    0
dise_code    0
cafe         0
title        0
name         0
date         0
contents     0
review       0
dtype: int64

In [16]:
df_rare_nervous_disorder03.isna().sum()

_id          0
dise_name    0
dise_code    0
cafe         0
title        0
name         0
date         0
contents     0
review       0
dtype: int64

In [17]:
df_rare_nervous_disorder04.isna().sum()

_id          0
dise_name    0
dise_code    0
cafe         0
title        0
name         0
date         0
contents     0
review       0
dtype: int64

In [18]:
df_rare_nervous_disorder05.isna().sum()

_id          0
dise_name    0
dise_code    0
cafe         0
title        0
name         0
date         0
contents     0
review       0
dtype: int64

In [19]:
# 모든 DataFrame을 열 방향으로 합치기
df_rare_nervous_disorder = pd.concat([df_rare_nervous_disorder01, df_rare_nervous_disorder02, df_rare_nervous_disorder03, df_rare_nervous_disorder04, df_rare_nervous_disorder05], ignore_index=True)

df_rare_nervous_disorder

_id    dise_name dise_code  \
0      66417aadc68fb6f104417c71       중증근무력증     G70.0   
1      66417ab5c68fb6f104417c73       중증근무력증     G70.0   
2      66417abcc68fb6f104417c75       중증근무력증     G70.0   
3      66417ac4c68fb6f104417c77       중증근무력증     G70.0   
4      66417acbc68fb6f104417c79       중증근무력증     G70.0   
...                         ...          ...       ...   
13291  6642c0d6205d240ea773906d  모세혈관확장성운동실조       G35   
13292  6642c1e14ceea7c26c01e340  모세혈관확장성운동실조       G35   
13293  6642c1e84ceea7c26c01e342  모세혈관확장성운동실조       G35   
13294  6642c1f14ceea7c26c01e344  모세혈관확장성운동실조       G35   
13295  6642c1f84ceea7c26c01e346  모세혈관확장성운동실조       G35   

                                       cafe  \
0                              ♥시험관아기 대표카페♥   
1      건강한 리서치 건강/ 미용/ 맛집 /서울 강남구 송파구 강서구 등   
2           스마트홀릭 ㅣ스사사맘스홀릭중고나라 여우야 딜공디매쇼핑테무   
3                                고양이라서 다행이야   
4                           폐암환우들과 그 가족의 모임   
...                                     ...   
13291                  아삭아삭 (원주 과일도소매/과일카페)   
13292                  아삭아삭 (원주 과일도소매/과일카페)   
13293                             ♬~수원맘 모여라   
13294   내보험속삭임 - 건강,암,태아,종신,치매,간병인,사망,수술비보험   
13295                  아삭아삭 (원주 과일도소매/과일카페)   

                                                   title    name  \
0                혹시, 복시(겹쳐보임)가 있거나 중증근무력증 진단 받으신 분 계실까요?  설탕친토마토   
1                 중증근무력증 치료 전문병원 시설 좋은곳 어디인지 아세요?(자료수집중)    자료정리   
2                                근력이 저하되는 중증 근무력증 알아 봅니다   미소의마법   
3                                                중증 근무력증     쌔랄라   
4                                항암중 중증근무력증 치료하신 분 계신가요?     묘성연   
...                                                  ...     ...   
13291  12/11~12/12 즐거운주말♬♬ 아삭이네 맛있는 과일 올라갑니다.﻿ 달콤한 가정...    아삭아삭   
13292                      1/25 화요일♬♬ 아삭이네 맛있는 과일 올라갑니다.    아삭아삭   
13293                  광교변비 탈출하기~ 장편한외과와 알아보는 반복되는 변비~!!   장편한외과   
13294        MG손해보험 ‘원더풀 종합보험’ 보험 하나로 100세까지 완벽 보장 받아보세요     모드니   
13295                                                              

                    date                                           contents  \
0      2024.03.20. 08:43  안녕하세요.\n채취 2회, 동결 5차를 앞두고 있습니다.\n얼마전? 그 이전부터 초...   
1      2024.05.01. 22:02  반갑습니다 ^^ 카페 여러분들 항상 잘 계시죠?\n이번 리서치는 중증근무력증 치료 ...   
2      2024.04.28. 08:28  근력이 저하되는 중증 근무력증은 근력이 감소하여 근육이 약해지고 기능이 저하되는 질...   
3      2023.07.21. 18:19  저희 아이가 최근 갑작스럽게 아파 입원중 입니다\nmri,ct 모두 정상이라 나오고...   
4      2023.08.30. 21:40  아버지께서 비소세포 편평상피 치료 4년차이십니다.\n20년도에 키트루다로 시작해서 ...   
...                  ...                                                ...   
13291  2021.12.10. 23:26  12/11~12/12 즐거운주말♬♬\n아삭이네 맛있는 과일 올라갑니다.\n한가지 안...   
13292  2022.01.25. 10:47  1/25 화요일♬♬\n아삭이네 맛있는 과일 올라갑니다.\n대량주문건으로 배송이 많이...   
13293  2022.02.21. 09:34  광교 변비 장편한외과\n새해를 지나면서 건강하고 아름다워지기 위해 헬스장 등에서 구...   
13294  2020.08.22. 23:05  MG손해보험 ‘원더풀 종합보험’\n보험 하나로 100세까지 완벽 보장 받아보세요\n...   
13295                                                                         

                                                  review  
0      [신경과에서 소론도정 처방받아서 증상 조절하고 있어요. 저같은 경우는 자연적으로 없...  
1      [중증근무력증 관련정보 찾는분 은근 계신것 같더라고요 다른 회원님들께 여쭤보시면 될...  
2      [▶테무 50만원 무료쇼핑 할인코드 ▶https://temu.com/s/1d3vDj...  
3      [바이러스 관련 가능성이 있으니\n\n그 쪽으로 사람 질병으로 검색도 해보세요..\...  
4      [복시가 있나요????전신중증근무력증은 초기에 복시가\n먼저 시작되는 경우가 많습니...  
...                                                  ...  
13291                                                     
13292                                                     
13293  [예약 하고가야되나요? 대장내시경 받은지 얼마 안됬는데 혈변을 보고 변비 설사 반복...  
13294                                                     
13295                                                 []  

[13296 rows x 9 columns]

In [20]:
# 중복값 제거
df_rare_nervous_disorder = drop_duplicates(df_rare_nervous_disorder, 'contents')
df_rare_nervous_disorder

_id    dise_name dise_code  \
0      66417aadc68fb6f104417c71       중증근무력증     G70.0   
1      66417ab5c68fb6f104417c73       중증근무력증     G70.0   
2      66417abcc68fb6f104417c75       중증근무력증     G70.0   
3      66417ac4c68fb6f104417c77       중증근무력증     G70.0   
4      66417acbc68fb6f104417c79       중증근무력증     G70.0   
...                         ...          ...       ...   
10750  6642ae93986e1adbfba2fe2a  모세혈관확장성운동실조     G11.3   
10751  6642ae9b986e1adbfba2fe2b  모세혈관확장성운동실조     G11.3   
10752  6642aea2986e1adbfba2fe2c  모세혈관확장성운동실조     G11.3   
10753  6642aeb1986e1adbfba2fe2e  모세혈관확장성운동실조     G11.3   
10754  6642aeb9986e1adbfba2fe2f  모세혈관확장성운동실조     G11.3   

                                       cafe  \
0                              ♥시험관아기 대표카페♥   
1      건강한 리서치 건강/ 미용/ 맛집 /서울 강남구 송파구 강서구 등   
2           스마트홀릭 ㅣ스사사맘스홀릭중고나라 여우야 딜공디매쇼핑테무   
3                                고양이라서 다행이야   
4                           폐암환우들과 그 가족의 모임   
...                                     ...   
10750      통합치유연구소[통치연] 심혈관/암/당뇨/자가면역/정신질환/   
10751                  암(만성병) 극복의 길을 찾는 사람들   
10752                              황정의 자연치유   
10753                                똑똑한투병기   
10754                             신라젠 주주 카페   

                                                   title    name  \
0                혹시, 복시(겹쳐보임)가 있거나 중증근무력증 진단 받으신 분 계실까요?  설탕친토마토   
1                 중증근무력증 치료 전문병원 시설 좋은곳 어디인지 아세요?(자료수집중)    자료정리   
2                                근력이 저하되는 중증 근무력증 알아 봅니다   미소의마법   
3                                                중증 근무력증     쌔랄라   
4                                항암중 중증근무력증 치료하신 분 계신가요?     묘성연   
...                                                  ...     ...   
10750                          스테로이드 호르몬 크림 장기 사용과 피부 문제    연구소장   
10751  [해외-영어책] Nutritional Oncology 영양 종양학 - 암 예방, 치...  꿈많은사람2   
10752                        어쩌면 혈이 전부다 2 (고혈압과 저혈압은.. )      카렌   
10753                      종양 표지자(tumor marker) 검사란 무엇인가  제3의 인생   
10754               "차세대 항암신약 트렌드 '면역' 이제 시작일뿐" (메디칼타임즈)      수호   

                    date                                           contents  \
0      2024.03.20. 08:43  안녕하세요.\n채취 2회, 동결 5차를 앞두고 있습니다.\n얼마전? 그 이전부터 초...   
1      2024.05.01. 22:02  반갑습니다 ^^ 카페 여러분들 항상 잘 계시죠?\n이번 리서치는 중증근무력증 치료 ...   
2      2024.04.28. 08:28  근력이 저하되는 중증 근무력증은 근력이 감소하여 근육이 약해지고 기능이 저하되는 질...   
3      2023.07.21. 18:19  저희 아이가 최근 갑작스럽게 아파 입원중 입니다\nmri,ct 모두 정상이라 나오고...   
4      2023.08.30. 21:40  아버지께서 비소세포 편평상피 치료 4년차이십니다.\n20년도에 키트루다로 시작해서 ...   
...                  ...                                                ...   
10750  2019.01.19. 14:50  스테로이드 호르몬 크림 장기 사용과 피부 문제\n\n\n습진, 건선, 아토피 피부염...   
10751  2021.12.27. 21:52  --- 작성자썰 ----\n*. 역시나, 바쁘신분들은 그냥 패스해주세요. 그냥 혼자...   
10752  2020.08.11. 18:52  서양의학이 아닌 동양 의학에서는\n건강 장수 할 수 있는 세가지 요건은\n결국 기가...   
10753  2020.07.21. 13:13  1. 종양표지자의 이용\n\n\n1) 암의 선별과 조기 진단 (Screening)\...   
10754  2018.05.26. 17:46  "차세대 항암신약 트렌드 '면역' 이제 시작일뿐"\n머크 임상책임자 "언멧니즈 여전...   

                                                  review  
0      [신경과에서 소론도정 처방받아서 증상 조절하고 있어요. 저같은 경우는 자연적으로 없...  
1      [중증근무력증 관련정보 찾는분 은근 계신것 같더라고요 다른 회원님들께 여쭤보시면 될...  
2      [▶테무 50만원 무료쇼핑 할인코드 ▶https://temu.com/s/1d3vDj...  
3      [바이러스 관련 가능성이 있으니\n\n그 쪽으로 사람 질병으로 검색도 해보세요..\...  
4      [복시가 있나요????전신중증근무력증은 초기에 복시가\n먼저 시작되는 경우가 많습니...  
...                                                  ...  
10750                                                     
10751  [정성에 감사드립니다., 🕵️😁탐구 정신, 한글 번역판이 이번에 출판된 것으로 알고...  
10752  [의사 리포트 읽는 것 같아요. ㅋ 그런데 귀에 쏙쏙 들어오네요. ㅋ, 넘 길지요?...  
10753               [감사합니다, 감사합니다\n잘읽었습니다, 좋은 자료 감사합니다♡]  
10754  [암에 대한 뉴스는 어마하게 쏟아지는군요.\n전 그저 신라젠만 보고 있습니다., 제...  

[10755 rows x 9 columns]

In [21]:
# 이상 data 처리
df_rare_nervous_disorder = df_rare_nervous_disorder[~df_rare_nervous_disorder['cafe'].str.contains('아반강고 힐링카페 아픈 반려 강아지와 고양이를 위한 힐링카페')]
df_rare_nervous_disorder = df_rare_nervous_disorder[~df_rare_nervous_disorder['cafe'].str.contains('아픈 반려 강아지와 고양이를 위한 힐링카페')]
df_rare_nervous_disorder = df_rare_nervous_disorder[~df_rare_nervous_disorder['cafe'].str.contains('강사모-반려견 훈련 교육법, 강아지 종류 유기견 입양 방법 안내')]
df_rare_nervous_disorder

_id    dise_name dise_code  \
0      66417aadc68fb6f104417c71       중증근무력증     G70.0   
1      66417ab5c68fb6f104417c73       중증근무력증     G70.0   
2      66417abcc68fb6f104417c75       중증근무력증     G70.0   
3      66417ac4c68fb6f104417c77       중증근무력증     G70.0   
4      66417acbc68fb6f104417c79       중증근무력증     G70.0   
...                         ...          ...       ...   
10750  6642ae93986e1adbfba2fe2a  모세혈관확장성운동실조     G11.3   
10751  6642ae9b986e1adbfba2fe2b  모세혈관확장성운동실조     G11.3   
10752  6642aea2986e1adbfba2fe2c  모세혈관확장성운동실조     G11.3   
10753  6642aeb1986e1adbfba2fe2e  모세혈관확장성운동실조     G11.3   
10754  6642aeb9986e1adbfba2fe2f  모세혈관확장성운동실조     G11.3   

                                       cafe  \
0                              ♥시험관아기 대표카페♥   
1      건강한 리서치 건강/ 미용/ 맛집 /서울 강남구 송파구 강서구 등   
2           스마트홀릭 ㅣ스사사맘스홀릭중고나라 여우야 딜공디매쇼핑테무   
3                                고양이라서 다행이야   
4                           폐암환우들과 그 가족의 모임   
...                                     ...   
10750      통합치유연구소[통치연] 심혈관/암/당뇨/자가면역/정신질환/   
10751                  암(만성병) 극복의 길을 찾는 사람들   
10752                              황정의 자연치유   
10753                                똑똑한투병기   
10754                             신라젠 주주 카페   

                                                   title    name  \
0                혹시, 복시(겹쳐보임)가 있거나 중증근무력증 진단 받으신 분 계실까요?  설탕친토마토   
1                 중증근무력증 치료 전문병원 시설 좋은곳 어디인지 아세요?(자료수집중)    자료정리   
2                                근력이 저하되는 중증 근무력증 알아 봅니다   미소의마법   
3                                                중증 근무력증     쌔랄라   
4                                항암중 중증근무력증 치료하신 분 계신가요?     묘성연   
...                                                  ...     ...   
10750                          스테로이드 호르몬 크림 장기 사용과 피부 문제    연구소장   
10751  [해외-영어책] Nutritional Oncology 영양 종양학 - 암 예방, 치...  꿈많은사람2   
10752                        어쩌면 혈이 전부다 2 (고혈압과 저혈압은.. )      카렌   
10753                      종양 표지자(tumor marker) 검사란 무엇인가  제3의 인생   
10754               "차세대 항암신약 트렌드 '면역' 이제 시작일뿐" (메디칼타임즈)      수호   

                    date                                           contents  \
0      2024.03.20. 08:43  안녕하세요.\n채취 2회, 동결 5차를 앞두고 있습니다.\n얼마전? 그 이전부터 초...   
1      2024.05.01. 22:02  반갑습니다 ^^ 카페 여러분들 항상 잘 계시죠?\n이번 리서치는 중증근무력증 치료 ...   
2      2024.04.28. 08:28  근력이 저하되는 중증 근무력증은 근력이 감소하여 근육이 약해지고 기능이 저하되는 질...   
3      2023.07.21. 18:19  저희 아이가 최근 갑작스럽게 아파 입원중 입니다\nmri,ct 모두 정상이라 나오고...   
4      2023.08.30. 21:40  아버지께서 비소세포 편평상피 치료 4년차이십니다.\n20년도에 키트루다로 시작해서 ...   
...                  ...                                                ...   
10750  2019.01.19. 14:50  스테로이드 호르몬 크림 장기 사용과 피부 문제\n\n\n습진, 건선, 아토피 피부염...   
10751  2021.12.27. 21:52  --- 작성자썰 ----\n*. 역시나, 바쁘신분들은 그냥 패스해주세요. 그냥 혼자...   
10752  2020.08.11. 18:52  서양의학이 아닌 동양 의학에서는\n건강 장수 할 수 있는 세가지 요건은\n결국 기가...   
10753  2020.07.21. 13:13  1. 종양표지자의 이용\n\n\n1) 암의 선별과 조기 진단 (Screening)\...   
10754  2018.05.26. 17:46  "차세대 항암신약 트렌드 '면역' 이제 시작일뿐"\n머크 임상책임자 "언멧니즈 여전...   

                                                  review  
0      [신경과에서 소론도정 처방받아서 증상 조절하고 있어요. 저같은 경우는 자연적으로 없...  
1      [중증근무력증 관련정보 찾는분 은근 계신것 같더라고요 다른 회원님들께 여쭤보시면 될...  
2      [▶테무 50만원 무료쇼핑 할인코드 ▶https://temu.com/s/1d3vDj...  
3      [바이러스 관련 가능성이 있으니\n\n그 쪽으로 사람 질병으로 검색도 해보세요..\...  
4      [복시가 있나요????전신중증근무력증은 초기에 복시가\n먼저 시작되는 경우가 많습니...  
...                                                  ...  
10750                                                     
10751  [정성에 감사드립니다., 🕵️😁탐구 정신, 한글 번역판이 이번에 출판된 것으로 알고...  
10752  [의사 리포트 읽는 것 같아요. ㅋ 그런데 귀에 쏙쏙 들어오네요. ㅋ, 넘 길지요?...  
10753               [감사합니다, 감사합니다\n잘읽었습니다, 좋은 자료 감사합니다♡]  
10754  [암에 대한 뉴스는 어마하게 쏟아지는군요.\n전 그저 신라젠만 보고 있습니다., 제...  

[10475 rows x 9 columns]

In [22]:
# title, contents 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
rare_nervous_disorder_series = df_rare_nervous_disorder['title'] + ' ' + df_rare_nervous_disorder['contents']
rare_nervous_disorder_series.isna().sum()

0

In [23]:
rare_nervous_disorder_list = rare_nervous_disorder_series.tolist()
rare_nervous_disorder_list

["혹시, 복시(겹쳐보임)가 있거나 중증근무력증 진단 받으신 분 계실까요? 안녕하세요.\n채취 2회, 동결 5차를 앞두고 있습니다.\n얼마전? 그 이전부터 초점이 안 맞아\n노안이라 생각하고 넘겼는데\n며칠전 정확하게 인지하게 됐습니다.\n오른쪽 특정 각도에서 겹쳐보여요\n어제 안과에서 시력,안압,망막 검사했는데\n다 정상인데 복시 증상이 있음\n대학병원에 가보라고 하셔 진료의뢰서를 받아왔습니다.\n겁나더라구요ㅜ\n찾아보니 시험관 하며 나타난 복시로\n시험관 중단하고 치료하시는 분들이 계시네요.\n그분들 진단은 '중증근무력증'입니다.\n더 겁나네요ㅠ\n혹시 복시 증상 나타나신 분 계신지\n계시면 자연호전 되셨는지 이야기 듣고 싶어\n글 올립니다.",
 '중증근무력증 치료 전문병원 시설 좋은곳 어디인지 아세요?(자료수집중) 반갑습니다 ^^ 카페 여러분들 항상 잘 계시죠?\n이번 리서치는 중증근무력증 치료 추천 잘하는곳 유명한곳에 대해서 물어보려고요*^^*\n우리는 살다보면 이렇게 필요에 의해서 다양한 경험을 구할 일이 생기기 마련이더라고요\n회원님들이나 이 질문글을 보시는 분들이 어쩌면 좋은 경험이나 정보를 알고 계신다면\n게시글에 댓글로 남겨주시면 글을 보시는 분들께 더없이 소중한 정보가 될것 같아요\n원래 이런 것들은 평소에는 필요 없다지만 급하게 찾으려면 정말 좋은 정보는 고르기가 어렵더라고요\n보통 중증근무력증 치료 같은 정보에 대해서 추천하는 곳이나 잘하는곳 유명한곳을 찾으려면\n그때마다 알아보거나 지인들에게 여쭤봐야 하는 경우가 발생되는데요\n그렇지만 의외로 검색해서 알아보면 최근 정보나, 내게 해당하는 정보를 찾기가 곤란하고\n막상 주변사람 중에 중증근무력증 치료 관련해서 어디를 추천 할껀지 어디가 잘하는곳으로 유명한곳인지 여쭤보면모르고 있는 경우가 훨씬 더 많거든요.\n그렇다고 SNS나 동영상 등에서 검색을 해봐도 자신에게 적합만 내용을 찾기란 쉽지 않더라고요\n그래서, 이렇게 카페에서 리서치를 통해 중증근무력증 치료 추천 유명한곳 잘하는곳에 대한

###### navercafe - 희귀질환 외 신경계 질환

In [24]:
df_nervous_disorder01 = dbconnect("naver_cafe_yujin_G00-G09")
df_nervous_disorder02 = dbconnect("naver_cafe_G00-G09")
df_nervous_disorder03 = dbconnect("naver_cafe_G10-G14")
df_nervous_disorder04 = dbconnect("naver_cafe_G20-G26")
df_nervous_disorder05 = dbconnect("naver_cafe_G40-G47")
df_nervous_disorder06 = dbconnect("naver_cafe_G80-G83")

In [25]:
# null값 확인
df_nervous_disorder01.isna().sum()

_id          0
dise_name    0
dise_code    0
cafe         0
title        0
name         0
date         0
contents     0
review       0
dtype: int64

In [26]:
# 두 DataFrame을 열 방향으로 합치기
df_nervous_disorder = pd.concat([df_nervous_disorder01, df_nervous_disorder02, df_nervous_disorder03, df_nervous_disorder04, df_nervous_disorder05, df_nervous_disorder06], ignore_index=True)

df_nervous_disorder

_id dise_name dise_code  \
0     6641dbe11637bfeab2b24930   세균성 수막염     G00.9   
1     6641dbe91637bfeab2b24931   세균성 수막염     G00.9   
2     6641dbf11637bfeab2b24932   세균성 수막염     G00.9   
3     6641dbf81637bfeab2b24933   세균성 수막염     G00.9   
4     6641dbff1637bfeab2b24934   세균성 수막염     G00.9   
...                        ...       ...       ...   
7497  66431871ccdb9249a0899ca8  강직성 뇌성마비     G80.0   
7498  6643187eccdb9249a0899ca9  강직성 뇌성마비     G80.0   
7499  6643188accdb9249a0899caa  강직성 뇌성마비     G80.0   
7500  66431892ccdb9249a0899cab  강직성 뇌성마비     G80.0   
7501  6643189accdb9249a0899cac  강직성 뇌성마비     G80.0   

                                      cafe  \
0                느린걸음(장애 보호자 및 재활 전문가 모임 )   
1                느린걸음(장애 보호자 및 재활 전문가 모임 )   
2      맘스홀릭 베이비 (330만 엄마들의 임신, 육아 지식in 카페)   
3      맘스홀릭 베이비 (330만 엄마들의 임신, 육아 지식in 카페)   
4     곰 마을 재테크 (월급쟁이,펀드,보험,주식,예적금,코인,부동산,)   
...                                    ...   
7497                               광남교회사랑해   
7498     물작메, 물리치료에 관한 작은 메모장, 물리치료, 물리치료사   
7499                        옹달샘 ♡ 중증아이care   
7500                                코어발란스핏   
7501      ╂학점플랜╂BEST사회복지사╂보육교사╂학사편입╂시간제수업╂   

                                                  title        name  \
0                                      바이러스성 / 세균성 뇌수막염          달맘   
1                                       37일 아기 세균성 뇌수막염       서율서아맘   
2     이유없는 고열 병원가니깐 뇌수막염 세균성 / 가와사키라는데 치료받으신분 계신가요 후...        뿌규라쀼   
3                                            4살 세균성뇌수막염     rkdgp03   
4                        태아보험 중증세균성수막염진단담보 큰 위험에 대비하세요~        다온맘s   
...                                                 ...         ...   
7497                                               건강상식         박기복   
7498                                          생화학 용어 정리  onlyjaejin   
7499                                           안녕하세요 :)    룩북86설이20   
7500                무정위 운동성(Athetosis type) 뇌성마비 아동의 치료   코어마스터 OSH   
7501                      [사회복지사][[장애인News]] 뇌성마비와 운동 2         오기곰   

                   date                                           contents  \
0     2022.01.11. 22:10  친구 아기가 지금 생후 70일 조금 넘었고, 2주전쯤 예방접종 맞은 후로 아기 컨디...   
1     2023.09.22. 11:14  생후 37일에 38.5도 고열로 인해 응급실 내원하였고 각종 검사 진행하였는데\n-...   
2     2024.04.15. 02:45  제목 그대로 이유없는 고열로 병원갔더니\n염증수치 8.6대로 정상범위보다 높긴 했지...   
3     2023.11.27. 21:23  단순히 감기겠지싶어서 5일동안 감기먹여도 열이 안떨어지고 머리가 너무아프다는 말에 ...   
4     2020.07.02. 13:51  <br />\n\n\n안녕하세요~\n보험판다 스탭다온맘s입니다~\n\n벌써 7월이네...   
...                 ...                                                ...   
7497  2011.02.04. 18:55  <FORM name=formBGM2><INPUT onchange=setVolume2...   
7498  2008.09.21. 23:50    L chain (경쇄, 경사슬, L쇄)\nL-amino acid oxidase ...   
7499  2022.10.23. 20:11  1. 닉네임변경 변경하셨나요?\n옹달샘(엄마출생년도)아이이름(아이출생년도) 아이이름...   
7500  2011.08.11. 10:09  1. 시작하는 말\n\n이 글은 근육 긴장도(muscle tone)의 기복이 있는\...   
7501  2007.02.14. 15:09  다음은 뇌성마비인들을 위한 활동내용과 방법들이다.\n\n① 근신장 운동 : 근 긴장...   

                                                 review  
0     [그러니까 말이에요 ㅜㅜ 그래서 일단 정확히 다시 물어보라구 했어요. 만에 하나 세...  
1     [안녕하세요. 저희는 생후 1일차에 숨이 가빠져서 대학병원 옮기는 도중에 열이 오르...  
2     [가와사키 작년 12월 진단후 완치 판정 받았어요! 휴우증은 없어요, ㅠㅠ 다행이네...  
3     [톼원 하셨나요?, 저희 아기도 세균성뇌수막염으로 입원중이에요.. 앞으로 3주는 더...  
4     [중증수막염 정말 위험하죠. 꼭 준비하셨음 좋겠어요 ~, 네!!맞아요..꼭 준비하셔...  
...                                                 ...  
7497  [☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆☆\n\n정관수술방법 관...  
7498                    [감사합니다.~, 감사합니다., biochemistry]  
7499  [안녕하세요 이곳에서 정보와 힐링 얻으셔요 반갑습니다, 네 감사합니다 :) 많은 정...  
7500                                                     
7501                                                     

[7502 rows x 9 columns]

In [27]:
# 중복값 제거
df_nervous_disorder = drop_duplicates(df_nervous_disorder, 'contents')
df_nervous_disorder

_id dise_name dise_code  \
0     6641dbe11637bfeab2b24930   세균성 수막염     G00.9   
1     6641dbe91637bfeab2b24931   세균성 수막염     G00.9   
2     6641dbf11637bfeab2b24932   세균성 수막염     G00.9   
3     6641dbf81637bfeab2b24933   세균성 수막염     G00.9   
4     6641dbff1637bfeab2b24934   세균성 수막염     G00.9   
...                        ...       ...       ...   
3878  66431807ccdb9249a0899c9d  강직성 뇌성마비     G80.0   
3879  66431838ccdb9249a0899ca2  강직성 뇌성마비     G80.0   
3880  6643184cccdb9249a0899ca4  강직성 뇌성마비     G80.0   
3881  66431854ccdb9249a0899ca5  강직성 뇌성마비     G80.0   
3882  6643185eccdb9249a0899ca6  강직성 뇌성마비     G80.0   

                                      cafe  \
0                느린걸음(장애 보호자 및 재활 전문가 모임 )   
1                느린걸음(장애 보호자 및 재활 전문가 모임 )   
2      맘스홀릭 베이비 (330만 엄마들의 임신, 육아 지식in 카페)   
3      맘스홀릭 베이비 (330만 엄마들의 임신, 육아 지식in 카페)   
4     곰 마을 재테크 (월급쟁이,펀드,보험,주식,예적금,코인,부동산,)   
...                                    ...   
3878     물작메, 물리치료에 관한 작은 메모장, 물리치료, 물리치료사   
3879                                앉다서다걷다   
3880                              darkeyes   
3881                                앉다서다걷다   
3882     물작메, 물리치료에 관한 작은 메모장, 물리치료, 물리치료사   

                                                  title     name  \
0                                      바이러스성 / 세균성 뇌수막염       달맘   
1                                       37일 아기 세균성 뇌수막염    서율서아맘   
2     이유없는 고열 병원가니깐 뇌수막염 세균성 / 가와사키라는데 치료받으신분 계신가요 후...     뿌규라쀼   
3                                            4살 세균성뇌수막염  rkdgp03   
4                        태아보험 중증세균성수막염진단담보 큰 위험에 대비하세요~     다온맘s   
...                                                 ...      ...   
3878                                          재활의학 필수용어     마미카르   
3879  경직성 양하지마비 아동과 엉덩이관절 탈구 - 치료 훈련중인 아동의 정형외과적 수술 ...     미소담은   
3880                                               뇌성마비      무공저   
3881                      재활훈련의 강도, 시간 그리고 휴식을 잘 고려하세요.     미소담은   
3882                                               신경해부  kky1516   

                   date                                           contents  \
0     2022.01.11. 22:10  친구 아기가 지금 생후 70일 조금 넘었고, 2주전쯤 예방접종 맞은 후로 아기 컨디...   
1     2023.09.22. 11:14  생후 37일에 38.5도 고열로 인해 응급실 내원하였고 각종 검사 진행하였는데\n-...   
2     2024.04.15. 02:45  제목 그대로 이유없는 고열로 병원갔더니\n염증수치 8.6대로 정상범위보다 높긴 했지...   
3     2023.11.27. 21:23  단순히 감기겠지싶어서 5일동안 감기먹여도 열이 안떨어지고 머리가 너무아프다는 말에 ...   
4     2020.07.02. 13:51  <br />\n\n\n안녕하세요~\n보험판다 스탭다온맘s입니다~\n\n벌써 7월이네...   
...                 ...                                                ...   
3878  2009.04.25. 22:57  - 아래 주의사항은 삭제하지 마시고, 게시글은 최하단에 올려주세요 -\n------...   
3879  2020.11.22. 05:40  미소담은재활운동연구소 박원장입니다.\n이번 글에서는 현재 제가 거의 5년간 소아재활...   
3880  2014.06.21. 23:46  뇌성마비 (한자: 腦性痲痺; 영어: cerebral palsy, CP)는 중추신경계...   
3881  2022.03.09. 02:27  그림1 몸통 근력 훈련\n그림2 몸통 근력 훈련\n그림3 보행 훈련\n소아재활훈련 ...   
3882  2007.07.20. 10:54  Anatomy an Vascular Territories of the Three M...   

                                                 review  
0     [그러니까 말이에요 ㅜㅜ 그래서 일단 정확히 다시 물어보라구 했어요. 만에 하나 세...  
1     [안녕하세요. 저희는 생후 1일차에 숨이 가빠져서 대학병원 옮기는 도중에 열이 오르...  
2     [가와사키 작년 12월 진단후 완치 판정 받았어요! 휴우증은 없어요, ㅠㅠ 다행이네...  
3     [톼원 하셨나요?, 저희 아기도 세균성뇌수막염으로 입원중이에요.. 앞으로 3주는 더...  
4     [중증수막염 정말 위험하죠. 꼭 준비하셨음 좋겠어요 ~, 네!!맞아요..꼭 준비하셔...  
...                                                 ...  
3878  [자료감사합니다. ^^, 감사해여 ^^, 감사합니다~~, 많군요 ㅋㅋ, 잘봣어요, ...  
3879  [이해하기 어려운 부분이 있지만 전문적인 내용이라 미처 몰랐던 많은 것을 알게 되었...  
3880                                                     
3881                                                     
3882  [제가 찾던 자료예요^^, 어렵네요ㅕㅜ 후후, 레퍼런스좀 알수있을까요???, 감사합...  

[3883 rows x 9 columns]

In [28]:
# 이상 data 처리
df_nervous_disorder = df_nervous_disorder[~df_nervous_disorder['cafe'].str.contains('아반강고 힐링카페 아픈 반려 강아지와 고양이를 위한 힐링카페')]
df_nervous_disorder

_id dise_name dise_code  \
0     6641dbe11637bfeab2b24930   세균성 수막염     G00.9   
1     6641dbe91637bfeab2b24931   세균성 수막염     G00.9   
2     6641dbf11637bfeab2b24932   세균성 수막염     G00.9   
3     6641dbf81637bfeab2b24933   세균성 수막염     G00.9   
4     6641dbff1637bfeab2b24934   세균성 수막염     G00.9   
...                        ...       ...       ...   
3878  66431807ccdb9249a0899c9d  강직성 뇌성마비     G80.0   
3879  66431838ccdb9249a0899ca2  강직성 뇌성마비     G80.0   
3880  6643184cccdb9249a0899ca4  강직성 뇌성마비     G80.0   
3881  66431854ccdb9249a0899ca5  강직성 뇌성마비     G80.0   
3882  6643185eccdb9249a0899ca6  강직성 뇌성마비     G80.0   

                                      cafe  \
0                느린걸음(장애 보호자 및 재활 전문가 모임 )   
1                느린걸음(장애 보호자 및 재활 전문가 모임 )   
2      맘스홀릭 베이비 (330만 엄마들의 임신, 육아 지식in 카페)   
3      맘스홀릭 베이비 (330만 엄마들의 임신, 육아 지식in 카페)   
4     곰 마을 재테크 (월급쟁이,펀드,보험,주식,예적금,코인,부동산,)   
...                                    ...   
3878     물작메, 물리치료에 관한 작은 메모장, 물리치료, 물리치료사   
3879                                앉다서다걷다   
3880                              darkeyes   
3881                                앉다서다걷다   
3882     물작메, 물리치료에 관한 작은 메모장, 물리치료, 물리치료사   

                                                  title     name  \
0                                      바이러스성 / 세균성 뇌수막염       달맘   
1                                       37일 아기 세균성 뇌수막염    서율서아맘   
2     이유없는 고열 병원가니깐 뇌수막염 세균성 / 가와사키라는데 치료받으신분 계신가요 후...     뿌규라쀼   
3                                            4살 세균성뇌수막염  rkdgp03   
4                        태아보험 중증세균성수막염진단담보 큰 위험에 대비하세요~     다온맘s   
...                                                 ...      ...   
3878                                          재활의학 필수용어     마미카르   
3879  경직성 양하지마비 아동과 엉덩이관절 탈구 - 치료 훈련중인 아동의 정형외과적 수술 ...     미소담은   
3880                                               뇌성마비      무공저   
3881                      재활훈련의 강도, 시간 그리고 휴식을 잘 고려하세요.     미소담은   
3882                                               신경해부  kky1516   

                   date                                           contents  \
0     2022.01.11. 22:10  친구 아기가 지금 생후 70일 조금 넘었고, 2주전쯤 예방접종 맞은 후로 아기 컨디...   
1     2023.09.22. 11:14  생후 37일에 38.5도 고열로 인해 응급실 내원하였고 각종 검사 진행하였는데\n-...   
2     2024.04.15. 02:45  제목 그대로 이유없는 고열로 병원갔더니\n염증수치 8.6대로 정상범위보다 높긴 했지...   
3     2023.11.27. 21:23  단순히 감기겠지싶어서 5일동안 감기먹여도 열이 안떨어지고 머리가 너무아프다는 말에 ...   
4     2020.07.02. 13:51  <br />\n\n\n안녕하세요~\n보험판다 스탭다온맘s입니다~\n\n벌써 7월이네...   
...                 ...                                                ...   
3878  2009.04.25. 22:57  - 아래 주의사항은 삭제하지 마시고, 게시글은 최하단에 올려주세요 -\n------...   
3879  2020.11.22. 05:40  미소담은재활운동연구소 박원장입니다.\n이번 글에서는 현재 제가 거의 5년간 소아재활...   
3880  2014.06.21. 23:46  뇌성마비 (한자: 腦性痲痺; 영어: cerebral palsy, CP)는 중추신경계...   
3881  2022.03.09. 02:27  그림1 몸통 근력 훈련\n그림2 몸통 근력 훈련\n그림3 보행 훈련\n소아재활훈련 ...   
3882  2007.07.20. 10:54  Anatomy an Vascular Territories of the Three M...   

                                                 review  
0     [그러니까 말이에요 ㅜㅜ 그래서 일단 정확히 다시 물어보라구 했어요. 만에 하나 세...  
1     [안녕하세요. 저희는 생후 1일차에 숨이 가빠져서 대학병원 옮기는 도중에 열이 오르...  
2     [가와사키 작년 12월 진단후 완치 판정 받았어요! 휴우증은 없어요, ㅠㅠ 다행이네...  
3     [톼원 하셨나요?, 저희 아기도 세균성뇌수막염으로 입원중이에요.. 앞으로 3주는 더...  
4     [중증수막염 정말 위험하죠. 꼭 준비하셨음 좋겠어요 ~, 네!!맞아요..꼭 준비하셔...  
...                                                 ...  
3878  [자료감사합니다. ^^, 감사해여 ^^, 감사합니다~~, 많군요 ㅋㅋ, 잘봣어요, ...  
3879  [이해하기 어려운 부분이 있지만 전문적인 내용이라 미처 몰랐던 많은 것을 알게 되었...  
3880                                                     
3881                                                     
3882  [제가 찾던 자료예요^^, 어렵네요ㅕㅜ 후후, 레퍼런스좀 알수있을까요???, 감사합...  

[3829 rows x 9 columns]

In [29]:
# title, contents 선택하여 합친 후 1개의 시리즈로 만들어서 list로 변환
df_nervous_disorder = df_nervous_disorder['title'] + ' ' + df_nervous_disorder['contents']
nervous_disorder_series.isna().sum()

NameError: name 'nervous_disorder_series' is not defined

In [ ]:
nervous_disorder_list = nervous_disorder_series.tolist()
nervous_disorder_list

##### 형태소 분석

In [ ]:
# 모든 자연어 list 합치기
total_lists = KMSS_list + dcinside_list + behcet_list
total_lists

###### 불용어 제거

In [ ]:
import re
patterns = '()'
series = []
for total_list in total_lists:
    total_list = str(total_list)
    text_regex = re.sub(pattern=patterns,repl='',string=total_list)
    if text_regex != '':
        series.append(text_regex)
series[:2]

In [ ]:
# 불용어 리스트 생성 (예시)
stopwords = ['자꾸','하루','신경섬유','지금','생각','이제','','갑자기','여기','사람','한번','오늘','그냥','희귀','가기','새끼','진짜' , '가끔','가든','가야','이번','제발','병신','시발','게이','dc','app','official','씨발','ㅆㅂ', '가', '고','좆', '을', '를', '이', '는']
from konlpy.tag import Okt

# Okt 형태소 분석기 인스턴스 생성
okt = Okt()

# 토크나이징 함수 정의
def tokenizer(raw, pos=["Noun", "Adverb", "Verb"], stopword=stopwords):
    return [
        word for word, tag in okt.pos(
            raw, 
            norm=True,   # normalize 그랰ㅋㅏ -> 그래ㅋㅋ
            stem=True    # stemming 바뀌나->바뀌다
            )
            if len(word) > 1 and tag in pos and word not in stopword
    ]

In [ ]:
# tokenizer
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer, TfidfTransformer
# tfidfVectorizer = TfidfVectorizer(tokenizer=tokenizer, max_df=0.95, min_df=2)
tfidfVectorizer = TfidfVectorizer(tokenizer=tokenizer, max_df=0.85, min_df=2)

In [ ]:
series = [' '.join(x.split()) for x in series]
features = tfidfVectorizer.fit_transform(series)
features.toarray()[:2]

###### LDA를 활용하여 Topic 추출

In [ ]:
import pyLDAvis
import pyLDAvis.lda_model
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import LatentDirichletAllocation

In [ ]:
components_3  = LatentDirichletAllocation(n_components=3, n_jobs=-1) # n_components => topic 가짓수 결정 / n_jobs =>성능높이기
components_3.fit(features)

In [ ]:
vis = pyLDAvis.lda_model.prepare(components_3, features, tfidfVectorizer) # 토픽모델, 교육이 끝난 값(행렬형태), 교육모델

In [ ]:
pyLDAvis.enable_notebook()
pyLDAvis.display(vis) # PCA - 차원축소